# 3D motion tracking using multiple cameras with OpenPose and Pose2Sim

<br>
<div align="center">Šárka Kadavá (kadava@leibniz-zas.de), Wim Pouw (wim.pouw@donders.ru.nl)</div>

<img src="Images/envision_banner.png" alt="isolated" width="300"/>

# Info documents

This python coding module shows how to perform 3D motion tracking on videos made with multiple cameras. Our contribution is aimed to provide a very easy python demo and pipeline that goes through the procedure start to end and is easily adaptable for processing in large batches (and where you already have data to work with). First, we get estimation of 2D coordinates using OpenPose. Afterwards, we calibrate the cameras using a checker board and we triangulate to get estimation of the coordinates in 3D space.

location Repository: https://github.com/sarkadava/demo_3Dtracking_pose2sim/tree/main

location Jupyter notebook: https://github.com/sarkadava/demo_3Dtracking_pose2sim/blob/main/openpose_to_pose2sim_tracking.ipynb

If you wish to record a setup with multiple cameras, you can check module: https://envisionbox.org/openpose_to_pose2sim_tracking.html


# Background

The code below first estimates the 2D coordinates of each video. 
Then it uses a video with checkerboard calibration from each of the camera and finds the angles between the cameras. 
Then we run Pose2Sim to triangulate the three videos to get coordinates in 3D space.

Note that we largely use material provided by OpenPose and Pose2sim creators.

citation for OpenPose: 

Cao, Z., Simon, T., Wei, S. E., & Sheikh, Y. (2017). Realtime multi-person 2d pose estimation using part affinity fields. In Proceedings of the IEEE conference on computer vision and pattern recognition (pp. 7291-7299).

citation for Pose2Sim: 

Pagnon, D., Domalain, M., & Reveret, L. (2022). Pose2Sim: An open-source Python package for multiview markerless kinematics. Journal of Open Source Software, 7(77), 4362.

Pagnon, D., Domalain, M., & Reveret, L. (2022). Pose2Sim: an end-to-end workflow for 3D markerless sports kinematics—part 2: accuracy. Sensors, 22(7), 2712.

Pagnon, D., Domalain, M., & Reveret, L. (2021). Pose2Sim: an end-to-end workflow for 3D markerless sports kinematics—part 1: robustness. Sensors, 21(19), 6530.


# Was this helpful?

citation for this module: Kadavá, S., Pouw, W. (2024). 3D motion tracking using multiple cameras with OpenPose and Pose2Sim [the day you viewed the site]. Retrieved from: xxx


# Requirements

Make sure you install the requirements.txt for running this module (pip install -r requirements.txt).

## After downloading the Github Repo
Once you have cloned the github repo, you dont have everything you need yet.

For the envision demo, please download:

* STEP1: the bin folder which would be in the openpose folder
* STEP2: the 135 model by following the link 'download_135model_EnvisionDemo' and place the 'pose_iter_XXXXXX.caffemodel' in the pose/body_135/ folder.

Now the larger files that are needed to run Open Pose are present and should now run when queried in the python code below.

For more information about the 135 keypoint Openpose pose model. We use this model as it is has the most amount of keypoints. It is however computationally heavy and we run this therefore with GPU support. But CPU should also work.

## Preparing the environment

First, we identify all the folders we will need.

In [1]:
import os
import subprocess
import glob

# this is the current working directorz
curfolder = os.path.abspath('./')

# this is the folder where openpose lives
openposefol = curfolder+'/openpose/'
openpose_demo_loc = curfolder+'/openpose/bin/OpenPoseDemo.exe'
# this is the model we are going to employ
model_to_employ = 'BODY_135'

# in this folder, we have our folders with videos (you can of course have multiple videos for multibatch processing)
folderstotrack = glob.glob(curfolder+'/projectdata/*')

print(folderstotrack)

['D:\\EnvisionBox_tracking\\demo_3Dtracking_pose2sim/projectdata\\trial_0']


## 2D tracking with OpenPose

OpenPose usually works with running the OpenPoseDemo.exe it in command prompt or terminal. Here we essentially write commands that will work as input to terminal, but we run it in python to keep our pipeline nice and linear.

In [2]:
def runcommand(command):
    # run the command using subprocess for OPENPOSE TRACKING
    try:
        subprocess.run(command, shell=True, check=True)
    except subprocess.CalledProcessError as e:
        print(f"Command execution failed with error code {e.returncode}")
    except FileNotFoundError:
        print("The OpenPoseDemo.exe executable was not found.")

# loop over the videofolders and prepare the folder structure
for i in folderstotrack:
    print(i)
    os.chdir(openposefol)
    # identify all avi files in folder
    direc = glob.glob(i + '/raw-2d/' +'*.avi')

    # 3 cameras
    video0 = direc[0]
    video1 = direc[1]
    video2 = direc[2]

    videolist = [video0, video1, video2]
    print(videolist)
    # make a new directory if it doesn't exist
    if not os.path.exists(i+'/pose-2d/'):
        os.makedirs(i+'/pose-2d/')
    if not os.path.exists(i+'/pose-2d/pose_cam1_json/'):
        os.makedirs(i+'/pose-2d/pose_cam1_json/')
    if not os.path.exists(i+'/pose-2d/pose_cam2_json/'):
        os.makedirs(i+'/pose-2d/pose_cam2_json/')
    if not os.path.exists(i+'pose-2d/pose_cam3_json/'):
        os.makedirs(i+'/pose-2d/pose_cam3_json/')
    # also make directory for openpose videos (pose-2d-trackingvideos)
    # make a new directory if it doesn't exist
    if not os.path.exists(i+'/pose-2d-trackingvideos/'):
        os.makedirs(i+'/pose-2d-trackingvideos/')

    # initialize the pose2 folder
    outputfol1 = i+'/pose-2d/pose_cam1_json/'
    outputfol2 = i+'/pose-2d/pose_cam2_json/'
    outputfol3 = i+'/pose-2d/pose_cam3_json/'

    outputfollist = [outputfol1, outputfol2, outputfol3]
    
    # loop over each video and perform motion tracking
    for it, j in enumerate(outputfollist):
        #first track with openpose vid1
        openposelocation = ' ' + openpose_demo_loc + ' '
        model = '--model_pose' + ' ' + model_to_employ + ' '
        video = '--video ' + videolist[it] + ' '
        todo = '--write_json '
        outputfol = j + ' '
        videoadd = '--write_video '
        videopath = i+'/pose-2d-trackingvideos/' + 'video'+str(it)+'.avi' + ' '
        command = r' '+openposelocation+model+video+todo+outputfol+videoadd+videopath
        print('were going to send this to command prompt: ' + command)
        runcommand(command)

D:\EnvisionBox_tracking\demo_3Dtracking_pose2sim/projectdata\trial_0
['D:\\EnvisionBox_tracking\\demo_3Dtracking_pose2sim/projectdata\\trial_0/raw-2d\\0_1_trial_1_raw_cam1.avi', 'D:\\EnvisionBox_tracking\\demo_3Dtracking_pose2sim/projectdata\\trial_0/raw-2d\\0_1_trial_1_raw_cam2.avi', 'D:\\EnvisionBox_tracking\\demo_3Dtracking_pose2sim/projectdata\\trial_0/raw-2d\\0_1_trial_1_raw_cam3.avi']
were going to send this to command prompt:   D:\EnvisionBox_tracking\demo_3Dtracking_pose2sim/openpose/bin/OpenPoseDemo.exe --model_pose BODY_135 --video D:\EnvisionBox_tracking\demo_3Dtracking_pose2sim/projectdata\trial_0/raw-2d\0_1_trial_1_raw_cam1.avi --write_json D:\EnvisionBox_tracking\demo_3Dtracking_pose2sim/projectdata\trial_0/pose-2d/pose_cam1_json/ --write_video D:\EnvisionBox_tracking\demo_3Dtracking_pose2sim/projectdata\trial_0/pose-2d-trackingvideos/video0.avi 
were going to send this to command prompt:   D:\EnvisionBox_tracking\demo_3Dtracking_pose2sim/openpose/bin/OpenPoseDemo.exe --m

## Check results openpose tracking videos
Openpose also allows you to visually inspect the tracking quality. Lets combine tracking videos and show them in the below python code.

In [3]:
#### Show output for deeplabcut videos side by side in one video, making one tracking video
import glob
from moviepy.editor import VideoFileClip, clips_array
from IPython.display import Video

vids = glob.glob(folderstotrack[0]+'/pose-2d-trackingvideos/' + "*.avi")

#### Load the video clips
video_clips = [VideoFileClip(vid) for vid in vids]

#### Concatenate the video clips horizontally
final_video = clips_array([video_clips])
output_path = os.path.abspath("../Images/temp/concatenated_video.mp4")
print(output_path)

final_video.write_videofile(output_path, codec='libx265',verbose= False, logger= None)
# Load the video clip
clip = VideoFileClip(output_path)
clip.ipython_display(width=480,verbose= False, logger= None)

D:\EnvisionBox_tracking\demo_3Dtracking_pose2sim\Images\temp\concatenated_video.mp4
Moviepy - Building video __temp__.mp4.
Moviepy - Writing video __temp__.mp4



Moviepy - Done !
Moviepy - video ready __temp__.mp4


Now we have 2D coordinates for each of the videos.

## 3D estimation

We will now calibrate the cameras to get their intrinsic and extrinsic angles, which will be used to triangulate the 2D kinematics to estimate 3D coordinate.

Again, we first load all the packages and set necessary folders

In [4]:
from Pose2Sim import Pose2Sim # key package pose2sim
from trc import TRCData # this is for working with trc opensim type datafiles
#common packages
import os
import subprocess
import glob
import pandas as pd
import os
import cv2
import numpy as np
import shutil

Note: NumExpr detected 16 cores but "NUMEXPR_MAX_THREADS" not set, so enforcing safe limit of 8.
NumExpr defaulting to 8 threads.


# Pose2sim presets

We will make use of specific settings for the pose2sim that are contained 'pose2simprjfolder'. Specifically you will find there a config.toml in the user folder, where you have important settings that have to do with the checker board calibration, the type of openpose model were using, the smoothing we want to apply. You can change these settings obviously. Please do check out the specific settings here: https://github.com/sarkadava/demo_3Dtracking_pose2sim/blob/main/Pose2Sim/Empty_project_ENVISION_settings/User/Config.toml

To fully understand them, please also go through the pose2sim documentation: https://github.com/perfanalytics/pose2sim

In [5]:
# what is the folder structure
pose2simprjfolder = curfolder+'/Pose2Sim/Empty_project_ENVISION_settings'
# here are stored videos
inputfolders = curfolder+'/projectdata/'
folderstotrack = glob.glob(curfolder+'/projectdata/*')

## Calibration and triangulation

Now we will calibrate using the 3 videos with checkerboard. Then we also perform the triangulation to get 3D coordinates. Note that you will also get an error estimate of the triangulation. 

To understand what these error values mean please go through the pose2sim documentation: https://github.com/perfanalytics/pose2sim

### The calibration
We have videos, and we create from that images, as input for calibration via pose2sim using a checkerboard. When the calibration is performed a .toml will be created in the calibration folder. This contains the intrinsic and extrinsic angle information of the cameras

### Triangulation
Subsequently the triangulation is performed and some post-processing (filtering) is applied as specified in the Config.toml that is copied into the folder from the [ENVISION template](https://github.com/sarkadava/demo_3Dtracking_pose2sim/blob/main/Pose2Sim/Empty_project_ENVISION_settings/User/Config.toml). 

In the pose-3d folder you will now find csv's and OpenSim files containing the 3D data. At some later point we will also go into opensim functionalities. For now the pipeline can be used to create 3D data.


In [6]:
# set framerate
framerate = 60

for i in folderstotrack:
    os.chdir(i)
    # get the sessionID
    split = i.split(os.path.sep)
    trialID = split[-1]
    sessionID = trialID.split("_")[-1]
    
    print(trialID)
    # copy a folder in pose2simprjfolder and its contents to folders and add it to another folder using shutil
    source1 = pose2simprjfolder+'/User/'
    source2 = pose2simprjfolder+'/opensim/'
    print('source = ' + source1 + ' to destination: ' + i+'/')
    # copy the user and opensim folder, but only if they don't exist
    if not os.path.exists(i+'/User/'):
        shutil.copytree(source1, i+'/User/')
    if not os.path.exists(i+'/opensim/'):
        shutil.copytree(source2, i+'/opensim/')

    print('calibration started')
    # calibration videos are only in the first folders of a session, so trial_0
    if '0' in trialID and not os.path.exists(i+'/calibration/Calib_checkerboard.toml'):
    # loop through the calibration folders with a video
    # then save every 10thm frame to an image in that folder 
        calib_folders = glob.glob(i+'/calibration/*')
        print(calib_folders)
        for c in calib_folders:
            # split the path into its components
            split = c.split(os.path.sep)
            camIndex = split[-1]
            input_video = c+'/'+sessionID+'_checker_'+camIndex+'.avi'
            cap = cv2.VideoCapture(input_video)

            # check if the video file was opened successfully
            if not cap.isOpened():
                print("Error: Couldn't open the video file.")
                exit()
            output_dir = c+'/'

            # frame counter
            frame_count = 0

            while True:
                # read the next frame
                ret, frame = cap.read()

                if not ret:
                    break  # break the loop if we reach the end of the video
                
                frame_count += 1

                # save every 10th frame
                if frame_count % 10 == 0:
                    frame_filename = f"{output_dir}frame_{frame_count}.png"
                    cv2.imwrite(frame_filename, frame)
                    print(f"Saved frame {frame_count}")

            # release the video capture object and close the video file
            cap.release()
            cv2.destroyAllWindows()
    
    # calibrate only if it is the first folder of a session
    if '0' in trialID: 
        # check if Calib_checkerboard.toml exists in the calibration folder
        if not os.path.exists(i+'/calibration/Calib_checkerboard.toml'):
            Pose2Sim.calibrateCams() # calibrate with checkerboard
    
    # else we copy the calibration files from the first folder
    else:
        # copy the calibration files from the first folder
        source = inputfolders+'trial_0'+'/calibration/'
        dest = i+'/calibration/'
        print('source = ' + source + ' to destination: ' + dest)
        # copy the calibration folder, but only with the .toml file
        if not os.path.exists(i+'/calibration/'):
            os.makedirs(i + '/calibration/')  # create the destination directory if it doesn't exist
        # if there is no toml file, copy it
        if not os.path.exists(i+'/calibration/Calib_checkerboard.toml'):
            for toml_file in glob.glob(source + 'Calib_checkerboard.toml'):
                shutil.copy(toml_file, dest)

    Pose2Sim.track2D()  # you want to keep 90% percent of the cameras?
    Pose2Sim.triangulate3D()
    Pose2Sim.filter3D()

    # check in the pose-3d folder\
    if not os.path.exists(i+'/pose-3d/'):
        os.makedirs(i+'/pose-3d/')
    posefolder = './pose-3d/'
    # check any .trc files in the folder
    trcfiles = glob.glob(posefolder + '*.trc')

    # loop through files and convert to csv
    for file in trcfiles:
        # now convert trc data to csv
        mocap_data = TRCData()
        mocap_data.load(os.path.abspath(file))

        num_frames = mocap_data['NumFrames']
        markernames = mocap_data['Markers'] # the marker names are not

        # convert movap_data to pandas dataframe
        mocap_data_df = pd.DataFrame(mocap_data, columns=mocap_data['Markers'])

        # each value within the dataframe consists a list of x,y,z coordinates, we want to seperate these out so that each marker and dimension has its own column
        # first we create a list of column names
        colnames = []
        for marker in markernames:
            colnames.append(marker + '_x')
            colnames.append(marker + '_y')
            colnames.append(marker + '_z')

        # Create a new DataFrame to store separated values
        new_df = pd.DataFrame()

        # Iterate through each column in the original DataFrame
        for column in mocap_data_df.columns:
            # Extract the x, y, z values from each cell
            xyz = mocap_data_df[column].tolist()
            # Create a new DataFrame with the values in the cell separated into their own columns
            xyz_df = pd.DataFrame(xyz, columns=[column + '_x', column + '_y', column + '_z'])
            # Add the new columns to the new DataFrame
            new_df = pd.concat([new_df, xyz_df], axis=1)

        # add a new time column to the new dataframe assuming the framerate was 60fps
        time = []
        ts = 0
        for i in range(0, int(num_frames)):
            ts = ts + 1/framerate
            time.append(ts)

        # add the time column to the new dataframe
        new_df['Time'] = time

        #write pd dataframe to csv
        new_df.to_csv(file+'.csv', index=False)



---------------------------------------------------------------------


trial_0
source = D:\EnvisionBox_tracking\demo_3Dtracking_pose2sim/Pose2Sim/Empty_project_ENVISION_settings/User/ to destination: D:\EnvisionBox_tracking\demo_3Dtracking_pose2sim/projectdata\trial_0/
calibration started


Tracking of the person of interest for trial_0, for all frames.
---------------------------------------------------------------------

Project directory: D:\EnvisionBox_tracking\demo_3Dtracking_pose2sim\projectdata\trial_0
100%|███████████████████████████████████████████████████████████████████████████████| 299/299 [00:01<00:00, 254.03it/s]

--> Mean reprojection error for Neck point on all frames is 20.2 px, which roughly corresponds to 99.4 mm. 
--> In average, 1.0 cameras had to be excluded to reach the demanded 20 px error threshold.

Tracked json files are stored in D:\EnvisionBox_tracking\demo_3Dtracking_pose2sim\projectdata\trial_0\pose-2d-tracked.
Tracking took 1.20 s.


---------------------------------------------------------------------
Triangulation of 2D points for trial_0, for all frames.
---------------------------------------------------------------------

Project directory: D:\EnvisionBox_tracking\demo_3Dtracking_pose2sim\projectdata\trial_0
100%|██████████████████████

In [12]:
# plot 
import pandas as pd
import matplotlib.pyplot as plt
from matplotlib.animation import FuncAnimation

# 3D tracking checking

MT_tracking = pd.read_csv(file+'.csv')
MT_tracking.head()